# C and Python
[Start in JupyterHub](https://jupyterhub.zdv.uni-mainz.de/hub/user-redirect/git-pull?repo=https://gitlab.rlp.net/fsvmatheinformatik/advancedpython&urlpath=tree/advancedpython/friday/CAndPython.ipynb&branch=master)

Python is a very high-level language and rather slow. But it is still possible to write your own fast code and execute it with Python as an interface. We will take a look at [`ctypes`](https://docs.python.org/3/library/ctypes.html) and [CFFI](https://cffi.readthedocs.io/en/latest/) as two ways to include your fast C-function into your python program.

In [14]:
# Create shared lib
!gcc -fPIC -shared pi.c -o libpiapprox.so

## `ctypes` 

In [22]:
from ctypes import *

libc = CDLL("libc.so.6") # cdll.msvcrt on Windows
print(libc.time(None))
printf = libc.printf
printf(b"%d bottles of beer\n", 42)

piapprox = CDLL("./libpiapprox.so")
pi_approx = piapprox.pi_approx
pi_approx.restype = c_float
print(pi_approx(5000))

1616426850
3.157599925994873


## CFFI

In [23]:
from cffi import FFI
ffibuilder = FFI()

ffibuilder.cdef("float pi_approx(int n);")

ffibuilder.set_source("_pi",  # name of the output C extension
"""
    #include "pi.h"
""",
    sources=['pi.c'],   # includes pi.c as additional sources
    libraries=['m'])    # on Unix, link with the math library

if __name__ == "__main__":
    ffibuilder.compile(verbose=True)

generating ./_pi.c
(already up-to-date)
the current directory is '/home/mavieth/Projects/advancedpython/friday'
running build_ext
building '_pi' extension
gcc -pthread -Wno-unused-result -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -fno-semantic-interposition -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -fPIC -I/usr/include/python3.9 -c _pi.c -o ./_pi.o
gcc -pthread -Wno-unused-result -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -fno-semantic-interposition -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -march=x86-64 -mtune=generic -O3 -pipe -fno-plt -fPIC -I/usr/include/python3.9 -c pi.c -o ./pi.o
gcc -pthread -shared -Wl,-O1,--sort-common,--as-needed,-z,relro,-z,now -fno-semantic-interposition -Wl,-O1,--sort-common,--as-needed,-z,relro,-z,now ./_pi.o ./pi.o -L/usr/lib -lm -o ./_pi.cpython-39-x86_64-linux-gnu.so


In [24]:
from _pi.lib import pi_approx

approx = pi_approx(10)
print(approx)

approx = pi_approx(10000)
print(approx)

3.200000047683716
3.159600019454956
